## Clustering Toronto Neighborhoods
### First, gather postal code information 
#### Available from Wikipedia: https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M

In [192]:
import pandas as pd
import numpy as np
link = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
tables = pd.read_html(link)

#the 1st table (tables[0]), and starting at the first line of that table (iloc[0:])
M_code = tables[0].iloc[0:]
M_code.columns = ['Postal Code', 'Borough', 'Neighbourhood']
M_code.head()

Postal Code           Borough              Neighbourhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

### Remove any postal codes where a neighbourhood has not been assigned

In [193]:
M_code['Borough'].replace('Not assigned', np.nan, inplace=True)
M_code.dropna(subset=['Borough'], axis=0, inplace=True)
print('The GTA has {} boroughs and {} neighbourhoods.'.format(len(M_code['Borough'].unique()),
        M_code.shape[0]))
M_code.head()

The GTA has 10 boroughs and 103 neighbourhoods.


/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/generic.py:6586: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._update_inplace(new_data)
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


Postal Code           Borough                                Neighbourhood
2         M3A        North York                                    Parkwoods
3         M4A        North York                             Victoria Village
4         M5A  Downtown Toronto                    Regent Park, Harbourfront
5         M6A        North York             Lawrence Manor, Lawrence Heights
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

### How many neighbourhoods remain in the dataset, stratified by borough?

In [194]:
M_code.groupby('Borough', axis=0).count()

Postal Code  Neighbourhood
Borough                                     
Central Toronto             9              9
Downtown Toronto           19             19
East Toronto                5              5
East York                   5              5
Etobicoke                  12             12
Mississauga                 1              1
North York                 24             24
Scarborough                17             17
West Toronto                6              6
York                        5              5

### Select the boroughs which include the name Toronto

In [195]:
Tdot_code = M_code.loc[M_code['Borough'].isin(['Central Toronto',
        'Downtown Toronto','East Toronto', 'West Toronto'])]
Tdot_code.reset_index(inplace=True)
Tdot_code.drop(['index'],axis=1,inplace=True)
Tdot_code.head(10)

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


Postal Code           Borough                                Neighbourhood
0         M5A  Downtown Toronto                    Regent Park, Harbourfront
1         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government
2         M5B  Downtown Toronto                     Garden District, Ryerson
3         M5C  Downtown Toronto                               St. James Town
4         M4E      East Toronto                                  The Beaches
5         M5E  Downtown Toronto                                  Berczy Park
6         M5G  Downtown Toronto                           Central Bay Street
7         M6G  Downtown Toronto                                     Christie
8         M5H  Downtown Toronto                     Richmond, Adelaide, King
9         M6H      West Toronto                 Dufferin, Dovercourt Village

In [196]:
Tdot_code.shape

(39, 3)

### Determine the latitude and the longitude coordinates of each neighborhood

In [197]:
df = pd.read_csv('http://cocl.us/Geospatial_data/Geospatial_Coordinates.csv')
df.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [ ]:
Tdot_code = pd.merge(Tdot_code, df)
Tdot_code.head()

Postal Code           Borough                                Neighbourhood  \
0         M5A  Downtown Toronto                    Regent Park, Harbourfront   
1         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   
2         M5B  Downtown Toronto                     Garden District, Ryerson   
3         M5C  Downtown Toronto                               St. James Town   
4         M4E      East Toronto                                  The Beaches   

    Latitude  Longitude  
0  43.654260 -79.360636  
1  43.662301 -79.389494  
2  43.657162 -79.378937  
3  43.651494 -79.375418  
4  43.676357 -79.293031

## Visualize the neighbourhoods on a map
#### Import packages required

In [ ]:
!conda install -c conda-forge folium=0.5.0 --yes
import folium # plotting library
print('Folium installed')

Solving environment: | 

#### Create map of Toronto using latitude and longitude values

In [94]:
latitude = 43.6532
longitude = -79.3832
map_tdot = folium.Map(location=[latitude, longitude], zoom_start=12)    
map_tdot

In [95]:
for lat, lng, borough, neighborhood in zip(Tdot_code['Latitude'], Tdot_code['Longitude'], Tdot_code['Borough'], Tdot_code['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_tdot)  
    
map_tdot

## Load Foursquare information for each neighbourhood
#### Client ID and password are hidden

In [63]:
# The code was removed by Watson Studio for sharing.

### Call venue information from Foursquare
#### Create function to call information from Foursquare API using client credentials, and neighbourhood geolocations in "Tdot_code" table

In [85]:
def getNearbyVenues(names, latitudes, longitudes, radius=800):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [86]:
import json 
import requests 
from pandas.io.json import json_normalize

In [87]:
LIMIT = 100
tdot_venues = getNearbyVenues(names=Tdot_code['Neighbourhood'],
                                   latitudes=Tdot_code['Latitude'],
                                   longitudes=Tdot_code['Longitude'])

Regent Park, Harbourfront
Queen's Park, Ontario Provincial Government
Garden District, Ryerson
St. James Town
The Beaches
Berczy Park
Central Bay Street
Christie
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
The Danforth West, Riverdale
Toronto Dominion Centre, Design Exchange
Brockton, Parkdale Village, Exhibition Place
India Bazaar, The Beaches West
Commerce Court, Victoria Hotel
Studio District
Lawrence Park
Roselawn
Davisville North
Forest Hill North & West, Forest Hill Road Park
High Park, The Junction South
North Toronto West, Lawrence Park
The Annex, North Midtown, Yorkville
Parkdale, Roncesvalles
Davisville
University of Toronto, Harbord
Runnymede, Swansea
Moore Park, Summerhill East
Kensington Market, Chinatown, Grange Park
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
R

In [88]:
print(tdot_venues.shape)
tdot_venues.head()

(2806, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Regent Park, Harbourfront               43.65426              -79.360636   
1  Regent Park, Harbourfront               43.65426              -79.360636   
2  Regent Park, Harbourfront               43.65426              -79.360636   
3  Regent Park, Harbourfront               43.65426              -79.360636   
4  Regent Park, Harbourfront               43.65426              -79.360636   

                    Venue  Venue Latitude  Venue Longitude  \
0        Roselle Desserts       43.653447       -79.362017   
1           Tandem Coffee       43.653559       -79.361809   
2          Impact Kitchen       43.656369       -79.356980   
3      Morning Glory Cafe       43.653947       -79.361149   
4  Cooper Koo Family YMCA       43.653249       -79.358008   

        Venue Category  
0               Bakery  
1          Coffee Shop  
2           Restaurant  
3       Breakfast Spot  
4  Distribution Center

### Add a yellow dot on the Toronto map for every venue called from Foursquare
#### Limit of 100 venues per neighbourhood

In [96]:
for lat, lng, venue, neighborhood in zip(tdot_venues['Venue Latitude'], tdot_venues['Venue Longitude'], tdot_venues['Venue Category'], tdot_venues['Neighborhood']):
    label = '{}, {}'.format(venue, neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        popup=label,
        color='yellow',
        fill=True,
        fill_opacity=0.7,
        parse_html=False).add_to(map_tdot)  
    
map_tdot

### Determine the frequecy of each 'venue category' per neighbourhood
#### Achieve this using onehot encoding to add dummy variables, and then determine frequency of total venues

In [99]:
print('There are {} uniques venue categories.'.format(len(tdot_venues['Venue Category'].unique())))

There are 289 uniques venue categories.


In [102]:
# one hot encoding
tdot_onehot = pd.get_dummies(tdot_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
tdot_onehot['Neighborhood'] = tdot_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [tdot_onehot.columns[-1]] + list(tdot_onehot.columns[:-1])
tdot_onehot = tdot_onehot[fixed_columns]

tdot_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport  \
0            0                  0                  0        0   
1            0                  0                  0        0   
2            0                  0                  0        0   
3            0                  0                  0        0   
4            0                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  ...  University  \
0                 0                    0  ...           0   
1                 0                    0  ...           0   
2                 0                    0  ...           0   
3                 0                    0  ...           0   
4                 0                    0  ...           0   

   Vegetarian / Vegan Restaurant  Video Game Store  Video Store  \
0                              0                 0            0   
1                              0                 0            0   
2                              0                 0            0   
3                              0                 0            0   
4                              0                 0            0   

   Vietnamese Restaurant  Whisky Bar  Wine Bar  Wine Shop  Wings Joint  \
0                      0           0         0          0            0   
1                      0           0         0          0            0   
2                      0           0         0          0            0   
3                      0           0         0          0            0   
4                      0           0         0          0            0   

   Women's Store  
0              0  
1              0  
2              0  
3              0  
4              0  

[5 rows x 289 columns]

In [105]:
tdot_grouped = tdot_onehot.groupby('Neighborhood').mean().reset_index()
tdot_grouped.head()

Neighborhood  Yoga Studio  \
0                                        Berczy Park     0.000000   
1       Brockton, Parkdale Village, Exhibition Place     0.000000   
2  Business reply mail Processing Centre, South C...     0.018182   
3  CN Tower, King and Spadina, Railway Lands, Har...     0.000000   
4                                 Central Bay Street     0.010000   

   Accessories Store  Afghan Restaurant  Airport  Airport Food Court  \
0           0.000000                0.0  0.00000             0.00000   
1           0.010204                0.0  0.00000             0.00000   
2           0.000000                0.0  0.00000             0.00000   
3           0.000000                0.0  0.03125             0.03125   
4           0.000000                0.0  0.00000             0.00000   

   Airport Gate  Airport Lounge  Airport Service  Airport Terminal  ...  \
0       0.00000          0.0000          0.00000           0.00000  ...   
1       0.00000          0.0000          0.00000           0.00000  ...   
2       0.00000          0.0000          0.00000           0.00000  ...   
3       0.03125          0.0625          0.09375           0.09375  ...   
4       0.00000          0.0000          0.00000           0.00000  ...   

   University  Vegetarian / Vegan Restaurant  Video Game Store  Video Store  \
0        0.00                       0.010000               0.0          0.0   
1        0.00                       0.010204               0.0          0.0   
2        0.00                       0.000000               0.0          0.0   
3        0.00                       0.000000               0.0          0.0   
4        0.01                       0.010000               0.0          0.0   

   Vietnamese Restaurant  Whisky Bar  Wine Bar  Wine Shop  Wings Joint  \
0                    0.0         0.0       0.0        0.0         0.00   
1                    0.0         0.0       0.0        0.0         0.00   
2                    0.0         0.0       0.0        0.0         0.00   
3                    0.0         0.0       0.0        0.0         0.00   
4                    0.0         0.0       0.0        0.0         0.01   

   Women's Store  
0            0.0  
1            0.0  
2            0.0  
3            0.0  
4            0.0  

[5 rows x 289 columns]

In [111]:
print ('In summary, there are {} unique categories of venues across {} neighbourhoods'.format(tdot_grouped.shape[1],tdot_grouped.shape[0]))

In summary, there are 289 unique categories of venues across 39 neighbourhoods


### Find the top 10 most common venues per neighbourhood

In [175]:
num_top_venues = 10

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [185]:
indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = tdot_grouped['Neighborhood']

for ind in np.arange(tdot_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(tdot_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Berczy Park           Coffee Shop   
1       Brockton, Parkdale Village, Exhibition Place           Coffee Shop   
2  Business reply mail Processing Centre, South C...  Fast Food Restaurant   
3  CN Tower, King and Spadina, Railway Lands, Har...       Harbor / Marina   
4                                 Central Bay Street           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Café                 Hotel   Japanese Restaurant   
1                  Café            Restaurant                Bakery   
2    Light Rail Station         Grocery Store           Coffee Shop   
3   Rental Car Location       Airport Service      Airport Terminal   
4                  Café        Clothing Store           Art Gallery   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0              Restaurant              Beer Bar                Bakery   
1  Furniture / Home Store   Arts & Crafts Store                   Bar   
2         Harbor / Marina               Brewery          Intersection   
3        Sculpture Garden         Boat or Ferry        Airport Lounge   
4     Japanese Restaurant      Ramen Restaurant                  Park   

  8th Most Common Venue  9th Most Common Venue 10th Most Common Venue  
0    Italian Restaurant     Seafood Restaurant            Art Gallery  
1             Gift Shop  Performing Arts Venue                   Park  
2    Italian Restaurant          Burrito Place                 Bakery  
3           Coffee Shop                  Plane                    Bar  
4         Grocery Store              Gastropub      French Restaurant

### Preliminary Clustering

In [186]:
from sklearn.cluster import KMeans

# set number of clusters
kclusters = 8
tdot_grouped_clustering = tdot_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(tdot_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([3, 1, 1, 5, 1, 1, 1, 3, 1, 1, 1, 3, 6, 3, 3, 1, 1, 1, 7, 1, 0, 1,
       1, 1, 3, 3, 4, 2, 1, 3, 1, 3, 1, 1, 1, 1, 1, 3, 1], dtype=int32)

#### Create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood

In [187]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

tdot_merged = Tdot_code

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
tdot_merged = tdot_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighbourhood')
tdot_merged.sort_values('Cluster Labels', ascending=True).head()

Postal Code           Borough  \
29         M4T   Central Toronto   
38         M7Y      East Toronto   
24         M5R   Central Toronto   
20         M4P   Central Toronto   
37         M4Y  Downtown Toronto   

                                        Neighbourhood   Latitude  Longitude  \
29                        Moore Park, Summerhill East  43.689574 -79.383160   
38  Business reply mail Processing Centre, South C...  43.662744 -79.321558   
24                The Annex, North Midtown, Yorkville  43.672710 -79.405678   
20                                   Davisville North  43.712751 -79.390197   
37                               Church and Wellesley  43.665860 -79.383160   

    Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
29               0                  Park         Grocery Store   
38               1  Fast Food Restaurant    Light Rail Station   
24               1                  Café           Coffee Shop   
20               1           Coffee Shop           Pizza Place   
37               1           Coffee Shop                  Café   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
29       Thai Restaurant        Sandwich Place  Gym / Fitness Center   
38         Grocery Store           Coffee Shop       Harbor / Marina   
24    Italian Restaurant                   Pub        Sandwich Place   
20    Italian Restaurant                  Café                   Gym   
37   Japanese Restaurant      Sushi Restaurant            Restaurant   

            6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
29                            Gym   Japanese Restaurant                  Café   
38                        Brewery          Intersection    Italian Restaurant   
24  Vegetarian / Vegan Restaurant           Pizza Place              Tea Room   
20                           Park              Pharmacy      Sushi Restaurant   
37                    Men's Store                  Park          Burger Joint   

   9th Most Common Venue 10th Most Common Venue  
29           Candy Store               Dive Bar  
38         Burrito Place                 Bakery  
24        History Museum     Mexican Restaurant  
20          Dessert Shop      Food & Drink Shop  
37         Grocery Store                Gay Bar

In [188]:
tdot_merged.sort_values('Cluster Labels', ascending=True).tail()

Postal Code           Borough  \
0          M5A  Downtown Toronto   
33         M4W  Downtown Toronto   
32         M5V  Downtown Toronto   
21         M5P   Central Toronto   
18         M4N   Central Toronto   

                                        Neighbourhood   Latitude  Longitude  \
0                           Regent Park, Harbourfront  43.654260 -79.360636   
33                                           Rosedale  43.679563 -79.377529   
32  CN Tower, King and Spadina, Railway Lands, Har...  43.628947 -79.394420   
21    Forest Hill North & West, Forest Hill Road Park  43.696948 -79.411307   
18                                      Lawrence Park  43.728020 -79.388790   

    Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0                3           Coffee Shop                  Park   
33               4                 Trail                  Park   
32               5       Harbor / Marina   Rental Car Location   
21               6    Italian Restaurant             Gastropub   
18               7            Restaurant             Bookstore   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0             Restaurant                Bakery                  Café   
33            Playground         Grocery Store                  Bank   
32       Airport Service      Airport Terminal      Sculpture Garden   
21                  Bank                Bakery  Gym / Fitness Center   
18                  Café           Coffee Shop  Gym / Fitness Center   

   6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
0                Theater                          Pub    Italian Restaurant   
33           Candy Store  Eastern European Restaurant     Electronics Store   
32         Boat or Ferry               Airport Lounge           Coffee Shop   
21              Pharmacy                   Bagel Shop           Coffee Shop   
18              Bus Line                         Park         Women's Store   

   9th Most Common Venue 10th Most Common Venue  
0         Cosmetics Shop        Thai Restaurant  
33   Dumpling Restaurant             Donut Shop  
32                 Plane                    Bar  
21   Japanese Restaurant                   Park  
18              Dive Bar                Dog Run

#### We can see many clusters are predominately driven by restaurants!

### Create a map of Toronto with the neighbourhoods clustered by venue category frequency

In [189]:
import matplotlib.cm as cm
import matplotlib.colors as colors

# create map of Manhattan using latitude and longitude values
map_tdot_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(tdot_merged['Latitude'], tdot_merged['Longitude'], tdot_merged['Neighbourhood'], tdot_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_tdot_clusters)
       
map_tdot_clusters

### What is the nature of each cluster?

In [190]:
tdot_merged.sort_values('Cluster Labels', ascending=True)

Postal Code           Borough  \
29         M4T   Central Toronto   
38         M7Y      East Toronto   
24         M5R   Central Toronto   
20         M4P   Central Toronto   
37         M4Y  Downtown Toronto   
25         M6R      West Toronto   
17         M4M      East Toronto   
26         M4S   Central Toronto   
15         M4L      East Toronto   
14         M6K      West Toronto   
27         M5S  Downtown Toronto   
12         M4K      East Toronto   
11         M6J      West Toronto   
28         M6S      West Toronto   
9          M6H      West Toronto   
7          M6G  Downtown Toronto   
6          M5G  Downtown Toronto   
30         M5T  Downtown Toronto   
4          M4E      East Toronto   
31         M4V   Central Toronto   
35         M4X  Downtown Toronto   
1          M7A  Downtown Toronto   
22         M6P      West Toronto   
23         M4R   Central Toronto   
19         M5N   Central Toronto   
16         M5L  Downtown Toronto   
13         M5K  Downtown Toronto   
10         M5J  Downtown Toronto   
8          M5H  Downtown Toronto   
5          M5E  Downtown Toronto   
3          M5C  Downtown Toronto   
34         M5W  Downtown Toronto   
2          M5B  Downtown Toronto   
36         M5X  Downtown Toronto   
0          M5A  Downtown Toronto   
33         M4W  Downtown Toronto   
32         M5V  Downtown Toronto   
21         M5P   Central Toronto   
18         M4N   Central Toronto   

                                        Neighbourhood   Latitude  Longitude  \
29                        Moore Park, Summerhill East  43.689574 -79.383160   
38  Business reply mail Processing Centre, South C...  43.662744 -79.321558   
24                The Annex, North Midtown, Yorkville  43.672710 -79.405678   
20                                   Davisville North  43.712751 -79.390197   
37                               Church and Wellesley  43.665860 -79.383160   
25                             Parkdale, Roncesvalles  43.648960 -79.456325   
17                                    Studio District  43.659526 -79.340923   
26                                         Davisville  43.704324 -79.388790   
15                     India Bazaar, The Beaches West  43.668999 -79.315572   
14       Brockton, Parkdale Village, Exhibition Place  43.636847 -79.428191   
27                     University of Toronto, Harbord  43.662696 -79.400049   
12                       The Danforth West, Riverdale  43.679557 -79.352188   
11                           Little Portugal, Trinity  43.647927 -79.419750   
28                                 Runnymede, Swansea  43.651571 -79.484450   
9                        Dufferin, Dovercourt Village  43.669005 -79.442259   
7                                            Christie  43.669542 -79.422564   
6                                  Central Bay Street  43.657952 -79.387383   
30          Kensington Market, Chinatown, Grange Park  43.653206 -79.400049   
4                                         The Beaches  43.676357 -79.293031   
31  Summerhill West, Rathnelly, South Hill, Forest...  43.686412 -79.400049   
35                        St. James Town, Cabbagetown  43.667967 -79.367675   
1         Queen's Park, Ontario Provincial Government  43.662301 -79.389494   
22                      High Park, The Junction South  43.661608 -79.464763   
23                  North Toronto West, Lawrence Park  43.715383 -79.405678   
19                                           Roselawn  43.711695 -79.416936   
16                     Commerce Court, Victoria Hotel  43.648198 -79.379817   
13           Toronto Dominion Centre, Design Exchange  43.647177 -79.381576   
10  Harbourfront East, Union Station, Toronto Islands  43.640816 -79.381752   
8                            Richmond, Adelaide, King  43.650571 -79.384568   
5                                         Berczy Park  43.644771 -79.373306   
3                                      St. James Town  43.651494 -79.375418   
34                                

#### cluster 0 = recreation; park and gyms
#### cluster 1 = food; coffee, cafés, restaurants
#### cluster 2 = recreation; playground & garden
#### cluster 3 = hospitality; coffee, cafés, hotels
#### cluster 4 = recreation; trail, park, playground
#### cluster 5 = harbour and airport
#### cluster 6 = restaurants and fitness
#### cluster 7 = restaurants, fitness, dog park


### End of Toronto Clustering Project